Importing Libraries

In [55]:
from selenium import webdriver #used to create a driver to scrape websites
#The following lines are used to import Service and Options classes specifically for Chrome from the selenium.webdriver.chrome module. Service is used to specify the path to the ChromeDriver executable, while Options allows you to set options for the Chrome browser.
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium_stealth import stealth
from selenium import webdriver
import os
import re
import time
import pandas as pd
import csv
import string
from datetime import datetime, timedelta
from webdriver_manager.chrome import ChromeDriverManager
import random
from datetime import datetime, timedelta
from sqlalchemy import create_engine


Defining Website to be Scraped

In [33]:
website = 'https://www.lyngsat.com/' #This line assigns the URL of the website you want to scrape to the variable website.
path = '/Users/youssef/Downloads/chromedriver-mac-arm64/chromedriver' #Here, the path where the ChromeDriver executable is located on your local machine is assigned to the variable path.

options = Options()  # This line creates an instance of the Options class, which can be used to set various options for the Chrome browser.
service = Service(ChromeDriverManager().install())  # This line creates a Service object, initialized with the path to the ChromeDriver executable. The Service object is used to manage the ChromeDriver server process.

driver = webdriver.Chrome(service=service, options=options)  # This line initializes the Chrome WebDriver, passing the service object (which includes the path to the ChromeDriver executable) and the options object (which includes browser options). This starts a new browser session controlled by the WebDriver.
stealth(driver,
        user_agent='Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/88.0.4324.150 Safari/537.36',
        languages=["en-US", "en"],
        vendor="Google Inc.",
        platform="Win32",
        webgl_vendor="Intel Inc.",
        renderer="Intel Iris OpenGL Engine",
        fix_hairline=False,  # Adjusted to False, change based on behavior
        )
time.sleep(2)
driver.get(website) #Finally, this line instructs the WebDriver to navigate to the URL stored in the website variable, effectively opening that page in the automated Chrome browser.
# driver.quit() This closes the browser or window, we must write a close for every .get() to avoid having a lot of open windows

Extracting Satellite Tables' links

In [34]:
satellite_regions = []
# Open the file and read the links
with open("SatelliteRegionsLinks.txt", "r", newline="") as Links:
    for line in Links:
        satellite_regions.append(line.strip())

Functions:

In [35]:
def extract_names(elements):
    temp = []  
    for element in elements:
        names = element.text
        if "(" in names:
            names = names[:names.index("(")].strip()
        temp.append(names)
    return temp

In [36]:
def extract_positionDegrees(elements):
    position_degrees = []
    for element in elements:
        full_text = element.text

        decimal_index = full_text.find('.')
        if decimal_index != -1:
            position_degree = full_text[:decimal_index + 2]  
            position_degrees.append(position_degree)
        else:
            position_degrees.append(full_text)
    return position_degrees

In [37]:
def extract_positionDirection(elements):
    position_directions = []
    for element in elements:
        full_text = element.text
        direction = full_text[-1:]
        position_directions.append(direction)
    return position_directions


In [38]:
def get_first_link_from_each_row(table_xpath):
    rows = driver.find_elements(By.XPATH, table_xpath + "/tr")
    links = []
    for row in rows:
        link_elements = row.find_elements(By.XPATH, ".//a")
        if link_elements:
            links.append(link_elements[0].get_attribute('href'))
    return links

In [39]:
def extract_substring(link):
    last_slash_index = link.rfind('/')
    html_index = link.find('.html', last_slash_index)
    
    if last_slash_index != -1 and html_index != -1:
        return link[last_slash_index + 1:html_index]
    return None


Extracting Satellites' names, positions, and links

In [40]:
Satnames = []
SatPositionDegree = []
SatPositionDirection = []
SatLinks = []
SatRegion = []

for link in satellite_regions:
    try:
        driver.get(link)
        WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.XPATH, '/html/body/div/table/tbody/tr/td/table[5]')))  
        
        
        
        # Determine the region for this page
        region = extract_substring(link)
        print(region)
        if region == 'asia':
            region = 'Asia & Pacific'
        elif region == 'europe':
            region = 'Europe, Africa & Middle East'
        elif region == 'atlantic':
            region = 'Atlantic'
        else:
            region = 'North & South America'
        print(region)

        # XPath for the left and right tables
        left_table_base_Xpath = '/html/body/div/table/tbody/tr/td[2]/table[5]/tbody/tr/td[1]/table/tbody'
        right_table_base_Xpath = '/html/body/div/table/tbody/tr/td[2]/table[5]/tbody/tr/td[2]/table/tbody'

        # Names
        name_elements = driver.find_elements(By.XPATH, left_table_base_Xpath + '/tr/td[2]')
        Satnames.extend(extract_names(name_elements))
        SatRegion.extend([region] * len(extract_names(name_elements)))
        
        name_elements = driver.find_elements(By.XPATH, right_table_base_Xpath + '/tr/td[2]')
        Satnames.extend(extract_names(name_elements))
        SatRegion.extend([region] * len(extract_names(name_elements)))

        # Positions
        position_elements = driver.find_elements(By.XPATH, left_table_base_Xpath + '/tr/td[1]')
        SatPositionDegree.extend(extract_positionDegrees(position_elements))
        
        position_elements = driver.find_elements(By.XPATH, right_table_base_Xpath + '/tr/td[1]')
        SatPositionDegree.extend(extract_positionDegrees(position_elements))

        # Directions
        SatPositionDirection.extend(extract_positionDirection(position_elements) * 2) 

        # Links
        SatLinks.extend(get_first_link_from_each_row(left_table_base_Xpath))
        SatLinks.extend(get_first_link_from_each_row(right_table_base_Xpath))

    except Exception as e:
        print(f"An error occurred: {e}")

driver.quit()

for i in range(len(Satnames)):
    print(Satnames[i])
    print(SatPositionDegree[i])
    print(SatPositionDirection[i])
    print(SatLinks[i])
    print(SatRegion[i])


asia
Asia & Pacific
europe
Europe, Africa & Middle East
atlantic
Atlantic
america
North & South America
TDRS 8
167.0
E
https://www.lyngsat.com/tracker/TDRS-8.html
Asia & Pacific
TDRS 10
171.0
E
https://www.lyngsat.com/tracker/TDRS-10.html
Asia & Pacific
TDRS 11
174.0
E
https://www.lyngsat.com/tracker/TDRS-11.html
Asia & Pacific
NSS 9
177.0
E
https://www.lyngsat.com/tracker/NSS-9.html
Asia & Pacific
Yamal 300K
177.0
E
https://www.lyngsat.com/tracker/Yamal-300K.html
Asia & Pacific
Intelsat 18
180.0
E
https://www.lyngsat.com/tracker/Intelsat-18.html
Asia & Pacific
NSS 11
176.0
E
https://www.lyngsat.com/tracker/NSS-11.html
Asia & Pacific
Eutelsat 174A
174.0
E
https://www.lyngsat.com/tracker/Eutelsat-174A.html
Asia & Pacific
Eutelsat 172B
172.0
E
https://www.lyngsat.com/tracker/Eutelsat-172B.html
Asia & Pacific
Horizons 3e
169.0
E
https://www.lyngsat.com/tracker/Horizons-3e.html
Asia & Pacific
Intelsat 5
166.1
E
https://www.lyngsat.com/tracker/Intelsat-5.html
Asia & Pacific
Luch 5A
166.0
E


Placing Links extracted from satellites in text file

In [41]:
filename = "SatelliteLinks.txt"


if os.path.exists(filename):
    os.remove(filename)


with open(filename, 'w') as file:
    for i, link_text in enumerate(SatLinks):
        if i > 0:
            file.write("\n")  
        file.write(link_text)

print(f"The link texts have been written to {filename}")



The link texts have been written to SatelliteLinks.txt


Reading Data Placed in File

In [42]:
SatelliteInfo = []
# Open the file and read the links
with open("SatelliteLinks.txt", "r", newline="") as Links:
    for line in Links:
        SatelliteInfo.append(line.strip())

Extracting launch_date and rocket

In [43]:
def extract_data(text):
    after_with_list = []
    before_period_list = []

    first_line_end_index = text.find('\n') if '\n' in text else len(text)
    first_period_index = text.find('.', 0, first_line_end_index)

    with_index = text.find('with ')
    if with_index != -1 and with_index < first_period_index:
        start_index = with_index + 5
        end_index = first_period_index - 11 if first_period_index != -1 and first_period_index - 11 > start_index else first_line_end_index
        after_with = text[start_index:end_index].strip()
        after_with_list.append(after_with)
    else:
        after_with_list.append("null")

    if first_period_index != -1 and first_period_index >= 10:
        before_period = text[first_period_index - 10:first_period_index].strip()
        before_period_list.append(before_period)
    else:
        before_period_list.append("null")

    return after_with_list, before_period_list

In [44]:
def execute_script_for_text(driver, xpath):
    return driver.execute_script("return document.evaluate(arguments[0], document, null, XPathResult.STRING_TYPE, null).stringValue.trim();", xpath)

In [45]:
SatRocket = []
SatLaunch_Date = []
driver2 = webdriver.Chrome(service=service, options=options)
stealth(driver2,
    languages=["en-US", "en"],
    vendor="Google Inc.",
    platform="Win32",
    webgl_vendor="Intel Inc.",
    renderer="Intel Iris OpenGL Engine",
    fix_hairline=True,
)

for link in SatelliteInfo:
    try:
        driver2.get(link)
        first_line_xpath = '/html/body/div/table/tbody/tr/td[2]/font/text()[1]'
        first_line_text = execute_script_for_text(driver2, first_line_xpath)
        if first_line_text:
            after_with, before_period = extract_data(first_line_text)
            SatRocket.extend(after_with)
            SatLaunch_Date.extend(before_period)
        else:
            SatRocket.append("null")
            SatLaunch_Date.append("null")

    except Exception as e:
        print(f"An error occurred while processing {link}: {e}")
        SatRocket.append("null")
        SatLaunch_Date.append("null")

driver2.quit()

In [46]:
for i in range(len(SatRocket)):
    print(SatRocket[i])
    print(SatLaunch_Date[i])

Atlas AC-139
2000-06-30
Atlas 2A - AC-144
2002-12-05
Atlas 5 - V401
2013-01-31
Ariane 5 - V187
2009-02-12
Proton
2012-11-02
Zenit 3/Baikonur
2011-10-05
Proton
2000-10-01
Proton
2005-12-29
Ariane 5 - VA237
2017-06-01
Ariane 5 - VA243
2018-09-25
Proton
1997-08-28
Proton
2011-12-11
Zenit 3/Sea Launch
2012-06-01
Ariane V125
1999-12-22
Proton
2003-11-24
Long March 3B
2022-11-05
Ariane 5 - VA242
2018-04-05
Ariane 5
2007-10-05
Proton
1999-09-26
Ariane 5 - V135
2000-11-16
Ariane 5 - V161
2003-06-11
Ariane 5 - V190
2009-08-21
Ariane 5 - VA218
2014-09-11
Ariane 4 - V141
2001-05-15
Falcon 9
2016-05-06
Ariane 5
2006-10-13
Ariane 5 - VA230
2016-06-18
Falcon 9
2019-12-17
Atlas 3B - AC-205
2003-04-12
Falcon 9
2019-02-22
Proton
2021-12-13
Falcon 9
2016-08-14
Ariane 5 - V185
2008-08-14
Xichang
2015-10-16
Proton
2013-12-26
Proton
2014-03-15
Falcon 9
2018-09-10
Ariane 5 - VA252
2020-02-18
Long March 3B
2020-07-09
Long March 3B
2018-05-03
Ariane 5 - V190
2009-08-21
Zenit 3
2006-04-12
Ariane 5
2008-04-18
A

Extracting Data-frame using pandas

In [47]:
print(len(Satnames))
print(len(SatLaunch_Date))
print(len(SatRocket))
print(len(SatPositionDegree))
print(len(SatPositionDirection))
print(len(SatRegion))

df = pd.DataFrame({"Name": Satnames, "Launch_Date": SatLaunch_Date, "Launch_Rocket": SatRocket, "PositionDegree": SatPositionDegree, "PositionDirection": SatPositionDirection, "Region": SatRegion}).to_csv("Satellites.csv", index=False) #index is having rows numbered 1,2,3,...
print(df)

366
366
366
366
366
366
None


Extracting Satellite Tables' links

In [261]:
channels_regions = []
# Open the file and read the links
with open("ChannelsRegionsLinks.txt", "r", newline="") as Links:
    for line in Links:
        channels_regions.append(line.strip())
        
for channel in channels_regions:
    print(channel)

https://www.lyngsat.com/asia.html
https://www.lyngsat.com/europe.html
https://www.lyngsat.com/atlantic.html
https://www.lyngsat.com/america.html


Extracting Link from website

In [292]:
ChannelSatLinks = []

options = Options()
service = Service(ChromeDriverManager().install())
driver3 = webdriver.Chrome(service=service, options=options)

stealth(driver3,
    languages=["en-US", "en"],
    vendor="Google Inc.",
    platform="Win32",
    webgl_vendor="Intel Inc.",
    renderer="Intel Iris OpenGL Engine",
    fix_hairline=True,
)

Xpath = '/html/body/div/table/tbody/tr/td[2]/table[5]/tbody/tr/td/table/tbody/tr/td/font/font/span/a'


try:
    for link in channels_regions:
        driver3.get(link)
        x = driver3.find_elements(By.XPATH, Xpath)
        for element in x:
            #print(element.get_attribute('href'))
            ChannelSatLinks.append(element.get_attribute('href'))
except Exception as e:
    print(f"An error occurred: {e}")
driver3.quit()
for i in range(len(ChannelSatLinks)):
    print(ChannelSatLinks[i])

https://www.lyngsat.com/NSS-9.html
https://www.lyngsat.com/Intelsat-18.html
https://www.lyngsat.com/Eutelsat-172B.html
https://www.lyngsat.com/Horizons-3e.html
https://www.lyngsat.com/Intelsat-19.html
https://www.lyngsat.com/ChinaSat-19.html
https://www.lyngsat.com/Superbird-B3.html
https://www.lyngsat.com/Optus-D2.html
https://www.lyngsat.com/ABS-6.html
https://www.lyngsat.com/Optus-D3.html
https://www.lyngsat.com/Optus-10.html
https://www.lyngsat.com/JCSAT-2B.html
https://www.lyngsat.com/Optus-D1.html
https://www.lyngsat.com/BRIsat.html
https://www.lyngsat.com/JCSAT-1C.html
https://www.lyngsat.com/Nusantara-Satu.html
https://www.lyngsat.com/Express-AMU7.html
https://www.lyngsat.com/JCSAT-16.html
https://www.lyngsat.com/Superbird-C2.html
https://www.lyngsat.com/Apstar-9.html
https://www.lyngsat.com/Express-AM5.html
https://www.lyngsat.com/Express-AT2.html
https://www.lyngsat.com/Telstar-18-Vantage.html
https://www.lyngsat.com/Apstar-6D.html
https://www.lyngsat.com/Apstar-6C.html
https

Adding Extracted Links into txt file

In [316]:
filename2 = "ChannelSat.txt"


if os.path.exists(filename2):
    os.remove(filename2)


with open(filename2, 'w') as file:
    for i, link_text in enumerate(ChannelSatLinks):
        if i > 0:
            file.write("\n")  
        file.write(link_text)

print(f"The link texts have been written to {filename2}")



The link texts have been written to ChannelSat.txt


In [64]:
ExtractedSatLinks = []
with open("ChannelSat.txt", "r", newline="") as Links:
    for line in Links:
        ExtractedSatLinks.append(line.strip())
for i in range(len(ExtractedSatLinks)):
    print(ExtractedSatLinks[i])

https://www.lyngsat.com/NSS-9.html
https://www.lyngsat.com/Intelsat-18.html
https://www.lyngsat.com/Eutelsat-172B.html
https://www.lyngsat.com/Horizons-3e.html
https://www.lyngsat.com/Intelsat-19.html
https://www.lyngsat.com/ChinaSat-19.html
https://www.lyngsat.com/Superbird-B3.html
https://www.lyngsat.com/Optus-D2.html
https://www.lyngsat.com/ABS-6.html
https://www.lyngsat.com/Optus-D3.html
https://www.lyngsat.com/Optus-10.html
https://www.lyngsat.com/JCSAT-2B.html
https://www.lyngsat.com/Optus-D1.html
https://www.lyngsat.com/BRIsat.html
https://www.lyngsat.com/JCSAT-1C.html
https://www.lyngsat.com/Nusantara-Satu.html
https://www.lyngsat.com/Express-AMU7.html
https://www.lyngsat.com/JCSAT-16.html
https://www.lyngsat.com/Superbird-C2.html
https://www.lyngsat.com/Apstar-9.html
https://www.lyngsat.com/Express-AM5.html
https://www.lyngsat.com/Express-AT2.html
https://www.lyngsat.com/Telstar-18-Vantage.html
https://www.lyngsat.com/Apstar-6D.html
https://www.lyngsat.com/Apstar-6C.html
https

Getting Links of Channels and Networks

In [261]:
driver4 = webdriver.Chrome(service=Service(ChromeDriverManager().install()), options=options)
ChannelLinks = []
NetworksLinks = []
PackageLinks = []

stealth(driver4,
    languages=["en-US", "en"],
    vendor="Google Inc.",
    platform="Win32",
    webgl_vendor="Intel Inc.",
    renderer="Intel Iris OpenGL Engine",
    fix_hairline=True,
)

ChannelXpath = '/html/body/div/table/tbody/tr/td[2]/table/tbody/tr/td/font/font[1]/b/a'
NetworkXpath = '/html/body/div/table/tbody/tr/td[2]/table/tbody/tr/td/font/font/b/i/a'
PackageXpath = '/html/body/div/table/tbody/tr/td[2]/table/tbody/tr/td/font/font/b/i/a'


try:
    for link in ExtractedSatLinks:
        driver4.get(link)
        channels = driver4.find_elements(By.XPATH, ChannelXpath)
        networks = driver4.find_elements(By.XPATH, NetworkXpath)
        packages = driver4.find_elements(By.XPATH, PackageXpath)
        for element in channels:
            href = element.get_attribute('href')
            if href and href.startswith("https://www.lyngsat.com/tvchannels") and href not in ChannelLinks:
                # print(href)
                ChannelLinks.append(href)
                
                
        for element2 in networks:
            href = element2.get_attribute('href')
            if href and href.startswith("https://www.lyngsat.com/providers") and href not in NetworksLinks:
                # print(href)
                NetworksLinks.append(href)
                
        for element3 in packages:
            href = element3.get_attribute('href')
            if href and href.startswith("https://www.lyngsat.com/packages") and href not in PackageLinks:
                print(href)
                PackageLinks.append(href)

except Exception as e:
    print(f"An error occurred: {e}")
driver4.quit()

https://www.lyngsat.com/packages/Canal---Caledonie.html
https://www.lyngsat.com/packages/Vini.html
https://www.lyngsat.com/packages/Sky-Pacific.html
https://www.lyngsat.com/packages/Sky-New-Zealand.html
https://www.lyngsat.com/packages/VAST.html
https://www.lyngsat.com/packages/Foxtel.html
https://www.lyngsat.com/packages/Sound-Planet.html
https://www.lyngsat.com/packages/Telekarta-140E.html
https://www.lyngsat.com/packages/NTV-Plus-Dalniy-Vostok.html
https://www.lyngsat.com/packages/D-Sky.html
https://www.lyngsat.com/packages/Mongolsat.html
https://www.lyngsat.com/packages/CBTV-Sat.html
https://www.lyngsat.com/packages/VTC-Digital.html
https://www.lyngsat.com/packages/K-.html
https://www.lyngsat.com/packages/AVG.html
https://www.lyngsat.com/packages/LaoSat-TV.html
https://www.lyngsat.com/packages/Sky-PerfecTV-128E.html
https://www.lyngsat.com/packages/Top-V-125E.html
https://www.lyngsat.com/packages/Digicel-Play.html
https://www.lyngsat.com/packages/Sky-PerfecTV-124E.html
https://www.

Placing Extracted Packages in file

In [262]:
filename5 = "PackageLinks.txt"
if os.path.exists(filename5):
    os.remove(filename5)

with open(filename5, 'w') as file:
    for i, link_text in enumerate(PackageLinks):
        if i > 0:
            file.write("\n")  
        file.write(link_text)

print(f"The link texts have been written to {filename5}")

The link texts have been written to PackageLinks.txt


Reading From the Extraced Packages

In [263]:
ExtractedPackageLinks = []
with open("PackageLinks.txt", "r", newline="") as Links:
    for line in Links:
        ExtractedPackageLinks.append(line.strip())
for i in range(len(ExtractedPackageLinks)):
    print(ExtractedPackageLinks[i])

https://www.lyngsat.com/packages/Canal---Caledonie.html
https://www.lyngsat.com/packages/Vini.html
https://www.lyngsat.com/packages/Sky-Pacific.html
https://www.lyngsat.com/packages/Sky-New-Zealand.html
https://www.lyngsat.com/packages/VAST.html
https://www.lyngsat.com/packages/Foxtel.html
https://www.lyngsat.com/packages/Sound-Planet.html
https://www.lyngsat.com/packages/Telekarta-140E.html
https://www.lyngsat.com/packages/NTV-Plus-Dalniy-Vostok.html
https://www.lyngsat.com/packages/D-Sky.html
https://www.lyngsat.com/packages/Mongolsat.html
https://www.lyngsat.com/packages/CBTV-Sat.html
https://www.lyngsat.com/packages/VTC-Digital.html
https://www.lyngsat.com/packages/K-.html
https://www.lyngsat.com/packages/AVG.html
https://www.lyngsat.com/packages/LaoSat-TV.html
https://www.lyngsat.com/packages/Sky-PerfecTV-128E.html
https://www.lyngsat.com/packages/Top-V-125E.html
https://www.lyngsat.com/packages/Digicel-Play.html
https://www.lyngsat.com/packages/Sky-PerfecTV-124E.html
https://www.

Extracting Channels From Packages

In [264]:
driverPackage = webdriver.Chrome(service=Service(ChromeDriverManager().install()), options=options)
PackageChannelLinks = []

stealth(driverPackage,
    languages=["en-US", "en"],
    vendor="Google Inc.",
    platform="Win32",
    webgl_vendor="Intel Inc.",
    renderer="Intel Iris OpenGL Engine",
    fix_hairline=True,
)

ChannelPackageXPath = '/html/body/div/table/tbody/tr/td[2]/table/tbody/tr/td/font/font/b/a'

try:
    i = 0
    for link in ExtractedPackageLinks:
        driverPackage.get(link)
        PackagedChannels = driverPackage.find_elements(By.XPATH, ChannelPackageXPath)
        for element in PackagedChannels:
            href = element.get_attribute('href')
            if href and href.startswith("https://www.lyngsat.com/tvchannels") and href not in ChannelLinks:
                print(href)
                ChannelLinks.append(href)
                i += 1
    print(f"Added: {i}")
except Exception as e:
    print(f"An error occurred: {e}")
driverPackage.quit()

https://www.lyngsat.com/tvchannels/fr/Serie-Club.html
https://www.lyngsat.com/tvchannels/fr/Planete---Crime.html
https://www.lyngsat.com/tvchannels/fr/Canal---Docs.html
https://www.lyngsat.com/tvchannels/fr/Cine---Frisson.html
https://www.lyngsat.com/tvchannels/fr/EMCI-TV-Europe.html
https://www.lyngsat.com/tvchannels/us/MTV-Hits-France.html
https://www.lyngsat.com/tvchannels/fr/Canal---Series-France.html
https://www.lyngsat.com/tvchannels/us/Disney-Channel-France.html
https://www.lyngsat.com/tvchannels/fr/MCM-France.html
https://www.lyngsat.com/tvchannels/fr/MGG-TV.html
https://www.lyngsat.com/tvchannels/fr/Planete---Aventure.html
https://www.lyngsat.com/tvchannels/fr/Cine---Famiz.html
https://www.lyngsat.com/tvchannels/us/Syfy-France.html
https://www.lyngsat.com/tvchannels/fr/InfoSport--.html
https://www.lyngsat.com/tvchannels/us/13eme-Rue.html
https://www.lyngsat.com/tvchannels/fr/Golf--.html
https://www.lyngsat.com/tvchannels/mu/MBC-Sat.html
https://www.lyngsat.com/tvchannels/fr/Te

In [265]:
def remove_elements_with_substring(elements, substring="info-card].html"):
    filtered_elements = [element for element in elements if substring not in element]
    return filtered_elements
filtered_elements = remove_elements_with_substring(ChannelLinks)

Adding Extracted Channel and Network links to txt files

In [266]:
filename3 = "ChannelLinks.txt"
filename4 = "NetworksLinks.txt"


ChannelLinks_unique = list(set(ChannelLinks))


if os.path.exists(filename3):
    os.remove(filename3)


with open(filename3, 'w') as file:
    file.write("\n".join(ChannelLinks_unique))  

print(f"The link texts have been written to {filename3}")


NetworksLinks_unique = list(set(NetworksLinks))


if os.path.exists(filename4):
    os.remove(filename4)


with open(filename4, 'w') as file:
    file.write("\n".join(NetworksLinks_unique))  

print(f"The link texts have been written to {filename4}")

The link texts have been written to ChannelLinks.txt
The link texts have been written to NetworksLinks.txt


Reading data from saved txt file

In [285]:
ExtractedChannelLinks = []
ExtractedNetworksLinks = []
with open("ChannelLinks.txt", "r", newline="") as Links:
    for line in Links:
        ExtractedChannelLinks.append(line.strip())
for i in range(len(ExtractedChannelLinks)):
    print(ExtractedChannelLinks[i])

with open("NetworksLinks.txt", "r", newline="") as Links:
    for line in Links:
        ExtractedNetworksLinks.append(line.strip())
for i in range(len(ExtractedNetworksLinks)):
    print(ExtractedNetworksLinks[i])



https://www.lyngsat.com/providers/au/ABC-SA.html
https://www.lyngsat.com/providers/fr/Mediawan-Thematics.html
https://www.lyngsat.com/providers/id/Indosat-Ooredoo-Hutchison.html
https://www.lyngsat.com/providers/tr/Profen.html
https://www.lyngsat.com/providers/cm/BT-Media-Group.html
https://www.lyngsat.com/providers/qa/Al-Kass.html
https://www.lyngsat.com/providers/br/Record-Litoral-e-Vale.html
https://www.lyngsat.com/providers/uk/Arqiva.html
https://www.lyngsat.com/providers/us/MASN.html
https://www.lyngsat.com/providers/ru/RTRS-Makhachkala.html
https://www.lyngsat.com/providers/br/Band-Amazonas.html
https://www.lyngsat.com/providers/ru/RTRS-Smolensk.html
https://www.lyngsat.com/providers/br/Rede-Bahia.html
https://www.lyngsat.com/providers/--/Rai-Way-Sicilia-1.html
https://www.lyngsat.com/providers/th/CAT-Telecom.html
https://www.lyngsat.com/providers/br/TV-Barriga-Verde.html
https://www.lyngsat.com/providers/us/PBS.html
https://www.lyngsat.com/providers/us/NASA-TV.html
https://www.l

In [195]:
# driver5 = webdriver.Chrome(service=Service(ChromeDriverManager().install()), options=options)
# 
# 
# stealth(driver5,
#     languages=["en-US", "en"],
#     vendor="Google Inc.",
#     platform="Win32",
#     webgl_vendor="Intel Inc.",
#     renderer="Intel Iris OpenGL Engine",
#     fix_hairline=True,
# )
# ChannelName = []
# ChannelWebsite = []
# ChannelCountries = []
# ChannelNameCountries = []
# RelatedChannels = []
# RelatedChannelName = []
# 
# ChannelNameXpath = '/html/body/div/table/tbody/tr/td[2]/table[1]/tbody/tr[1]/td/font/b/font'
# ChannelWebsiteXpath1 = '/html/body/div/table/tbody/tr/td[2]/table[5]/tbody/tr/td[1]/font[1]/a'
# ChannelWebsiteXpath2 = '/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[1]/font[1]/a'
# 
# CountryXpaths = [
#     '/html/body/div/table/tbody/tr/td[2]/table[5]/tbody/tr/td[1]/font[2]/a',
#     '/html/body/div/table/tbody/tr/td[2]/table[5]/tbody/tr/td[1]/font[2]/a[1]',
#     '/html/body/div/table/tbody/tr/td[2]/table[5]/tbody/tr/td[1]/font[2]/a[2]',
#     '/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[1]/font[2]/a',
#     '/html/body/div/table/tbody/tr/td[2]/table[5]/tbody/tr/td[1]/font/a'
# ]
# 
# 
# RelatedChannelsXpath = '/html/body/div/table/tbody/tr/td[2]/p/table[1]/tbody/tr/td/font/span/a'
# 
# 
# try:
#     chindex = 0
#     for link in ExtractedChannelLinks:
#         driver5.get(link)
#         
#         # Find the channel name
#         chindex += 1
#         chname_elements = driver5.find_elements(By.XPATH, ChannelNameXpath)
#         channel_name = chname_elements[0].text if chname_elements else "Unknown"
#         Final_name = channel_name
#         print("=================================")
#         print(f"Proposed Channel: {channel_name}")
#         print("=================================")
#         if channel_name not in ChannelName:
#             ChannelName.append(Final_name)
#             print(Final_name)
#         else:
#             country_name = ''
#             for xpath in CountryXpaths:
#                 chcountry_elements = driver5.find_elements(By.XPATH, xpath)
#                 if len(chcountry_elements) == 0:
#                     country_name = "Unknown " + chindex 
#                 for element in chcountry_elements:
#                     if element.get_attribute('href').startswith("https://www.lyngsat.com/freetv"):
#                         country_name = element.text
#                         break
#                     else:
#                         country_name = "Unknown " + chindex
#             Final_name = channel_name + " " + country_name
#             ChannelName.append(Final_name)
#             print(Final_name)
#                     
#         # print(Final_name)
# 
#         # Find the channel website and check if it's not a lyngsat free TV link
#         chweb_elements = driver5.find_elements(By.XPATH, ChannelWebsiteXpath1) or driver5.find_elements(By.XPATH, ChannelWebsiteXpath2)
#         if chweb_elements and not chweb_elements[0].get_attribute('href').startswith("https://www.lyngsat.com/freetv"):
#             website_url = chweb_elements[0].get_attribute('href')
#         else:
#             website_url = "null"
#         ChannelWebsite.append(website_url)
#         print(website_url)
# 
#         # Find channel countries
#         found_countries = set()
#         for xpath in CountryXpaths:
#             chcountry_elements = driver5.find_elements(By.XPATH, xpath)
#             for element in chcountry_elements:
#                 if element.get_attribute('href').startswith("https://www.lyngsat.com/freetv"):
#                     country_name = element.text
#                     found_countries.add(country_name)
# 
#         # If no country is found, use the default
#         if not found_countries:
#             found_countries.add("Unknown")
# 
#         # Append the found countries and replicate the channel name accordingly
#         ChannelCountries.extend(found_countries)
#         ChannelNameCountries.extend([Final_name] * len(found_countries))
#         # print([Final_name] * len(found_countries))
#         # print(found_countries)
# 
#         # Find related channels
#         found_related_channels = set()
#         related_channel_elements = driver5.find_elements(By.XPATH, RelatedChannelsXpath)
#         for element in related_channel_elements:
#             related_channel_name = element.text
#             if element.get_attribute('href').startswith("https://www.lyngsat.com/tvchannels"):
#                 found_related_channels.add(related_channel_name)
#             
# 
#         if found_related_channels:
#             RelatedChannels.extend(found_related_channels)
#             RelatedChannelName.extend([Final_name] * len(found_related_channels))
#             # print([Final_name] * len(found_related_channels))
#             # print(found_related_channels)
#         else:
#             # Default related channel to the current channel name if none found
#             RelatedChannels.append(Final_name)
#             RelatedChannelName.append(Final_name)
#             # print(Final_name)
#             # print(Final_name)
#     
#         
# except Exception as e:
#     print(f"An error occurred: {e}")
# finally:
#     driver5.quit()

Proposed Channel: AFN Prime Pacific
AFN Prime Pacific
https://myafn.dodmedia.osd.mil/
Proposed Channel: AFN News
AFN News
https://myafn.dodmedia.osd.mil/
Proposed Channel: AFN Sports
AFN Sports
https://myafn.dodmedia.osd.mil/
Proposed Channel: KGTF
KGTF
https://pbsguam.org/
Proposed Channel: BYU TV Global
BYU TV Global
https://www.byutv.org/
Proposed Channel: AFN Prime Atlantic
AFN Prime Atlantic
https://myafn.dodmedia.osd.mil/
Proposed Channel: AFN Spectrum
AFN Spectrum
https://myafn.dodmedia.osd.mil/
Proposed Channel: AFN Sports 2
AFN Sports 2
https://myafn.dodmedia.osd.mil/
Proposed Channel: AFN Family
AFN Family
https://myafn.dodmedia.osd.mil/
Proposed Channel: AFN Movie
AFN Movie
https://myafn.dodmedia.osd.mil/
Proposed Channel: AFN Guide
AFN Guide
https://myafn.dodmedia.osd.mil/
Proposed Channel: ABC Australia Pacific
ABC Australia Pacific
http://www.abcaustralia.net.au/
Proposed Channel: MTN Special Events
MTN Special Events
null
Proposed Channel: MSNBC International
MSNBC Inter

Extracting Channel Attributes

In [131]:
# for i in range(len(ChannelWebsite)):
#         if i < len(ChannelName):
#             print(f" {ChannelName[i]} has website Website: {ChannelWebsite[i]}")
#             print("=======================")
#         if i >= len(ChannelName):
#             print(f"out of range websites: {ChannelWebsite[i]}")
# # for i in range(len(ChannelWebsite)):
# #     print(ChannelWebsite[i])
# #     
# # # for i in range(len(ChannelName)):
# # #     print(ChannelName[i])

 AFN Prime Pacific has website Website: https://myafn.dodmedia.osd.mil/
 AFN News has website Website: https://myafn.dodmedia.osd.mil/
 AFN Sports has website Website: https://myafn.dodmedia.osd.mil/
 KGTF has website Website: https://pbsguam.org/
 BYU TV Global has website Website: https://www.byutv.org/
 AFN Prime Atlantic has website Website: https://myafn.dodmedia.osd.mil/
 AFN Spectrum has website Website: https://myafn.dodmedia.osd.mil/
 AFN Sports 2 has website Website: https://myafn.dodmedia.osd.mil/
 AFN Family has website Website: https://myafn.dodmedia.osd.mil/
 AFN Movie has website Website: https://myafn.dodmedia.osd.mil/
 AFN Guide has website Website: https://myafn.dodmedia.osd.mil/
 ABC Australia Pacific has website Website: http://www.abcaustralia.net.au/
 MTN Special Events has website Website: null
 MSNBC International has website Website: https://www.msnbc.com/
 Fox News Channel has website Website: http://www.foxnews.com/
 CNBC US has website Website: https://www.c

Placing Extracted Data in CSV files:

In [196]:
# print(f"Channel names: {len(ChannelName)}")
# print(f"Websites: {len(ChannelWebsite)}")
# print(f"Countries: {len(ChannelCountries)}")
# print(f"Channel names for countries: {len(ChannelNameCountries)}")
# print(f"Total Related channels: {len(RelatedChannels)}")
# print(f"Total Related channel names: {len(RelatedChannelName)}")
# 
# df_channel = pd.DataFrame({"Name": ChannelName, "Website": ChannelWebsite}).drop_duplicates()
# df_channel.to_csv("Channel.csv", index=False)
# print(f"Unique channel entries: {len(df_channel)}")
# 
# df_countries = pd.DataFrame({"ChannelName": ChannelNameCountries, "Countries": ChannelCountries}).drop_duplicates()
# df_countries.to_csv("ChannelCountries.csv", index=False)
# print(f"Unique channel-country entries: {len(df_countries)}")
# 
# df_related = pd.DataFrame({"ChannelName": RelatedChannelName, "RelatedChannels": RelatedChannels}).drop_duplicates()
# df_related.to_csv("ChannelRelatedChannels.csv", index=False)
# print(f"Unique related channel entries: {len(df_related)}")

Channel names: 8782
Websites: 8782
Countries: 9398
Channel names for countries: 9398
Total Related channels: 86883
Total Related channel names: 86883
Unique channel entries: 8782
Unique channel-country entries: 9398
Unique related channel entries: 86877


Cleaning Extracted Data

In [ ]:
# def process_duplicates_in_csv(input_file_path, output_file_path):
#     with open(input_file_path, mode='r', newline='') as file:
#         reader = csv.DictReader(file)
#         rows = list(reader)  # Read all data from the CSV file
# 
#     # Count occurrences of each name
#     name_counts = defaultdict(int)
#     for row in rows:
#         name_counts[row['Name']] += 1
# 
#     # Modify duplicate names
#     updated_rows = []
#     seen_counts = defaultdict(int)  # Track how many times we've seen each name
#     for row in rows:
#         name = row['Name']
#         if name_counts[name] > 1:
#             seen_counts[name] += 1
#             name += f" {seen_counts[name]}"  # Append the count to the name
#         updated_rows.append({**row, 'Name': name})
# 
#     # Write the updated data to a new file
#     with open(output_file_path, mode='w', newline='') as file:
#         writer = csv.DictWriter(file, fieldnames=reader.fieldnames)
#         writer.writeheader()
#         writer.writerows(updated_rows)
# 
# 
# process_duplicates_in_csv('Channel.csv', 'Channel2.csv')

Extracting Data to use in Channel table

In [272]:
driver6 = webdriver.Chrome(service=Service(ChromeDriverManager().install()), options=options)


stealth(driver6,
    languages=["en-US", "en"],
    vendor="Google Inc.",
    platform="Win32",
    webgl_vendor="Intel Inc.",
    renderer="Intel Iris OpenGL Engine",
    fix_hairline=True,
)

ChannelName = []
ChannelNameSing = []
ChannelNameXpath = '/html/body/div/table/tbody/tr/td[2]/table[1]/tbody/tr[1]/td/font/b/font'

SatelliteName = []
SatelliteXpath = ['/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[2]/font/span/a', '/html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr/td[2]/font/span/a']

# /html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr[3]/td[2]/font/span/a
# /html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr[4]/td[2]/font/span/a
# /html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr[5]/td[2]/font/span/a
# /html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr[3]/td[2]/font/span/a
# /html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr[3]/td[2]/font/span/a
#/html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr[4]/td[2]/font/span/a

Unwanted_XPath = ['/html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr/td[2]/font/a', '/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[2]/font/a']

Frequency = []
FrequencyXpath = ['/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[4]/font', '/html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr/td[4]/font']

# /html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr[3]/td[4]/font/a
# /html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr[5]/td[4]/font/a
# /html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr[10]/td[4]/font/a
# /html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr[4]/td[4]/font/a
# /html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr[16]/td[2]/font/a
ChannelWebsite = []
ChannelWebsiteXpath1 = '/html/body/div/table/tbody/tr/td[2]/table[5]/tbody/tr/td[1]/font[1]/a'
ChannelWebsiteXpath2 = '/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[1]/font[1]/a'

# /html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr[2]/td[3]/font/b/text()[1]
# /html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr[2]/td[3]/font/b/text()[1]
Beam = []
BeamXpath = ['/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[3]/font', '/html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr/td[3]/font']    
# /html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr[3]/td[3]/font
EIRP = []

SR = []
SRXpath = ['/html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr/td[6]/font', '/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[6]/font']
# /html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr[3]/td[6]/font/text()[1]
# /html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr[14]/td[6]/font/text()
# /html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr[3]/td[6]/font/text()[1]
# /html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr[3]/td[6]/font/text()
# /html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr[4]/td[6]/font/text()[1]

FEC = []
# /html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr[3]/td[6]/font/text()[2]
# /html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr[28]/td[6]/font/text()[2]
# /html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr[3]/td[6]/font/text()[2]
# /html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr[4]/td[6]/font/text()[2]


VideoCompression = []
VideoCompressionXpath = ['/html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr/td[7]/font', '/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[7]/font']


VideoEncoding = []

#-------------------------------------------------------------------------------------------------------------------

ChannelSystemName = []
ChannelSystemSat = []
ChannelSystemFreq = []
ChannelSystemVideoEncod = []
ChannelSystem = []
SystemXpath = ['/html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr/td[5]/font', '/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[5]/font']

ChannelLanguageName = []
ChannelLanguageSat = []
ChannelLanguageFreq = []
ChannelLanguageVideoEncod = []
ChannelLanguage= []
LanguageXpath = ['/html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr/td[8]/font', '/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[8]/font']


ChannelEncryptionName =[]
ChannelEncryptionSat = []
ChannelEncryptionFreq = []
ChannelEncryptionVideoEncod = []
ChannelEncryption = []
EncryptionXpath = ['/html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr/td[9]/font', '/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[9]/font']

ChannelCountriesName =[]
ChannelCountriesSat = []
ChannelCountriesFreq = []
ChannelCountriesVideoEncod = []
ChannelCountries = []
CountryXpaths = [
    '/html/body/div/table/tbody/tr/td[2]/table[5]/tbody/tr/td[1]/font[2]/a',
    '/html/body/div/table/tbody/tr/td[2]/table[5]/tbody/tr/td[1]/font[2]/a[1]',
    '/html/body/div/table/tbody/tr/td[2]/table[5]/tbody/tr/td[1]/font[2]/a[2]',
    '/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[1]/font[2]/a',
    '/html/body/div/table/tbody/tr/td[2]/table[5]/tbody/tr/td[1]/font/a'
]

maxLoops = 0
try:
    for link in ExtractedChannelLinks:
        if maxLoops > 15912:
            break
        driver6.get(link)
        temp_SatName = []
        temp_freq = []
        
        
        i =0
        for xpath in SatelliteXpath:
            satellite_elements = driver6.find_elements(By.XPATH, xpath)
            for satellite_element in satellite_elements:
                satellite_link = satellite_element.get_attribute('href')
                if not satellite_link.startswith('https://www.lyngsat.com/stream'):
                    i = i +1
                    Satname = satellite_element.text
                    SatelliteName.append(satellite_element.text)
                    temp_SatName.append(satellite_element.text)
                    # print(satellite_element.text)
        j = 0
        chname_elements = driver6.find_elements(By.XPATH, ChannelNameXpath)
        channel_name = chname_elements[0].text if chname_elements else "Unknown"
        channel_name = channel_name
        while j < i:
            ChannelName.append(channel_name)
            # print(channel_name)
            j += 1
     
        for xpath in FrequencyXpath:
            frequecny_elements = driver6.find_elements(By.XPATH, xpath)
            for frequency_element in frequecny_elements:
                if frequency_element.text != "Frequency":
                    Frequency.append(frequency_element.text)
                    temp_freq.append(frequency_element.text)
                    FrequencyEl = frequency_element.text
                    # print(frequency_element.text)
        
        j = 0
        chweb_elements = driver6.find_elements(By.XPATH, ChannelWebsiteXpath1) or driver6.find_elements(By.XPATH, ChannelWebsiteXpath2)
        if chweb_elements and not chweb_elements[0].get_attribute('href').startswith("https://www.lyngsat.com/freetv"):
            website_url = chweb_elements[0].get_attribute('href')
        else:
            website_url = "null"
        while j < i:
            ChannelWebsite.append(website_url)
            # print(website_url)
            j += 1
        
        

        for xpath in VideoCompressionXpath:
            video_elements = driver6.find_elements(By.XPATH, xpath)
            for video_element in video_elements:
                if video_element.text != 'Video':
                    video_text = video_element.text.strip()
                    
                    video_compression = "Unknown"
                    video_encoding = "Unknown"
            
                    if video_text:
                        parts = video_text.split('\n')
                        if len(parts) > 0:
                            # If the part contains 'SD' or 'HD', it's likely encoding.
                            if "SD" in parts[0] or "HD" in parts[0]:
                                video_encoding = parts[0]
                            else:
                                video_compression = parts[0]
                            
                        if len(parts) > 1:
                            video_encoding = parts[1]
            
                    
                    VideoCompression.append(video_compression)
                    VideoEncoding.append(video_encoding)
                    
                    # print(f'Video Compression: {video_compression}')
                    # print(f'Video Encoding: {video_encoding}')
        
           
        for xpath in BeamXpath:
            Beam_elements = driver6.find_elements(By.XPATH, xpath)
            j = 0
            for Beam_element in Beam_elements:
                if Beam_element.text != 'Beam\nEIRP (dBW)':
                    Beam_text = Beam_element.text.strip()
                        
                    if not Beam_text:
                        if j < i:
                            Beam.append("null")
                            EIRP.append("null")
                            # print(f'Beam: null')
                            # print(f'EIRP: null')
                            j += 1
                    else:
                        parts = Beam_text.split('\n')
                        
                        if len(parts) == 2:
                            if j < i:
                                Beam.append(parts[0])
                                EIRP.append(parts[1])
                                # print(f'Beam: {parts[0]}')
                                # print(f'EIRP: {parts[1]}')
                                j += 1
                        elif len(parts) == 1:
                            if parts[0][0].isdigit():
                                if j < i:
                                    EIRP.append(parts[0])
                                    Beam.append("null")
                                    # print(f'Beam: null')
                                    # print(f'EIRP: {parts[0]}')
                                    j += 1
                            else:
                                if j < i:
                                    Beam.append(parts[0])
                                    EIRP.append("null")
                                    # print(f'Beam: {parts[0]}')
                                    # print(f'EIRP: null')
                                    j += 1

                        
        for xpath in SRXpath:
            sr_fec_elements = driver6.find_elements(By.XPATH, xpath)
            for sr_fec_element in sr_fec_elements:
                if sr_fec_element.text != "SR\nFEC":
                    text = sr_fec_element.text.strip()
                    
                    
                    sr = "null"
                    fec = "null"
                    
                    
                    parts = text.split('\n')
                    
                    
                    if len(parts) > 0 and any(char.isdigit() for char in parts[0]):
                        sr = parts[0]
                    
                    
                    if len(parts) > 1 and (any(char.isdigit() for char in parts[1]) or '/' in parts[1]):
                        fec = parts[1]
    
                   
                    SR.append(sr)
                    FEC.append(fec)
    
                    # print(f'SR: {sr}, FEC: {fec}')
    
        found_countries = set()
        for xpath in CountryXpaths:
            chcountry_elements = driver6.find_elements(By.XPATH, xpath)
            for element in chcountry_elements:
                if element.get_attribute('href').startswith("https://www.lyngsat.com/freetv"):
                    country_name = element.text
                    found_countries.add(country_name)

       
        if not found_countries:
            found_countries.add("Unknown")

        
        ChannelCountries.extend(found_countries)
        ChannelCountriesName.extend([channel_name] * len(found_countries))
        # print([channel_name] * len(found_countries))
        ChannelCountriesSat.extend([Satname] * len(found_countries))
        # print([Satname] * len(found_countries))
        ChannelCountriesFreq.extend([FrequencyEl] * len(found_countries))
        # print([FrequencyEl] * len(found_countries))
        ChannelCountriesVideoEncod.extend([video_encoding] * len(found_countries))
        # print([video_encoding] * len(found_countries))
        # print(found_countries)
        

        index = 0            
        for xpath in SystemXpath:
            system_elements = driver6.find_elements(By.XPATH, xpath)
            for system_element in system_elements:
                systemCount = 0
                if system_element.text != 'System':
                    system_text = system_element.text.strip()
                    
                    
                    parts = system_text.split('\n') if system_text else []
                    if len(parts) == 2:  
                        ChannelSystem.append(parts[0])  
                        ChannelSystem.append(parts[1])  
                        systemCount += 2
                        # print(f'System: {parts[0]}')
                        # print(f'System: {parts[1]}')
                        ChannelSystemName.append(channel_name)
                        ChannelSystemName.append(channel_name)
                        # print(channel_name)
                        # print(channel_name)
                        ChannelSystemSat.append(temp_SatName[index])
                        ChannelSystemSat.append(temp_SatName[index])
                        # print(temp_SatName[index])
                        # print(temp_SatName[index])
                        ChannelSystemFreq.append(temp_freq[index])
                        ChannelSystemFreq.append(temp_freq[index])
                        # print(temp_freq[index])
                        # print(temp_freq[index])
                        ChannelSystemVideoEncod.append(VideoEncoding[index])
                        ChannelSystemVideoEncod.append(VideoEncoding[index])
                        # print(VideoEncoding[index])
                        # print(VideoEncoding[index])
                        # print('==============')
                    elif len(parts) == 1:  
                        ChannelSystem.append(parts[0])  
                        # print(f'System: {parts[0]}')
                        ChannelSystemName.append(channel_name)
                        # print(channel_name)
                        ChannelSystemSat.append(temp_SatName[index])
                        # print(temp_SatName[index])
                        ChannelSystemFreq.append(temp_freq[index])
                        # print(temp_freq[index])
                        ChannelSystemVideoEncod.append(VideoEncoding[index])
                        # print(VideoEncoding[index])
                        # print('==============')
                        systemCount += 1
                    else:  # If the cell is empty, append "Unknown" once.
                        ChannelSystem.append("Unknown")
                        ChannelSystemName.append(channel_name)
                        # print(channel_name)
                        ChannelSystemSat.append(temp_SatName[index])
                        # print(temp_SatName[index])
                        ChannelSystemFreq.append(temp_freq[index])
                        # print(temp_freq[index])
                        ChannelSystemVideoEncod.append(VideoEncoding[index])
                        # print(VideoEncoding[index])
                        # print('System: Unknown')
                        # print('==============')
                    index += 1
        index = 0
        for xpath in LanguageXpath:
            Language_elements = driver6.find_elements(By.XPATH, xpath)
            for Lang_element in Language_elements:
                if Lang_element.text != 'Lang.':
                    Lang_text = Lang_element.text.strip()
                    
                    
                    parts = list(set(Lang_text.split('\n'))) if Lang_text else []
                    i = 0
                    
                    if len(parts) >= 2:  
                        for i in range (len(parts)): 
                            ChannelLanguage.append(parts[i])  
                            # print(f'Lang: {parts[i]}')
                            ChannelLanguageName.append(channel_name)
                            # print(channel_name)
                            ChannelLanguageSat.append(temp_SatName[index])
                            # print(temp_SatName[index])
                            ChannelLanguageFreq.append(temp_freq[index])
                            # print(temp_freq[index])
                            ChannelLanguageVideoEncod.append(VideoEncoding[index])
                            # print(VideoEncoding[index])
                        # print('==============')
                    elif len(parts) == 1:  
                        ChannelLanguage.append(parts[0])  
                        # print(f'Lang: {parts[0]}')
                        # print(channel_name)
                        ChannelLanguageName.append(channel_name)
                        ChannelLanguageSat.append(temp_SatName[index])
                        # print(temp_SatName[index])
                        ChannelLanguageFreq.append(temp_freq[index])
                        # print(temp_freq[index])
                        ChannelLanguageVideoEncod.append(VideoEncoding[index])
                        # print(VideoEncoding[index])
                        # print('==============')
                    else:  
                        ChannelLanguage.append("Unknown")
                        # print(f'Lang: Unknown')
                        ChannelLanguageName.append(channel_name)
                        # print(channel_name)
                        ChannelLanguageSat.append(temp_SatName[index])
                        # print(temp_SatName[index])
                        ChannelLanguageFreq.append(temp_freq[index])
                        # print(temp_freq[index])
                        ChannelLanguageVideoEncod.append(VideoEncoding[index])
                        # print(VideoEncoding[index])
                        # print('==============')
                    index += 1
                    
        index = 0
        for xpath in EncryptionXpath:
            Encryption_elements = driver6.find_elements(By.XPATH, xpath)
            for Encryption_element in Encryption_elements:
                if Encryption_element.text != 'Encryption':
                    Encryption_text = Encryption_element.text.strip()
                    
                    
                    parts = list(set(Encryption_text.split('\n'))) if Encryption_text else []
                    i = 0
                    
                    if len(parts) >= 2: 
                        for i in range (len(parts)): 
                            ChannelEncryption.append(parts[i])  
                            #print(f'Encryp: {parts[i]}')
                            ChannelEncryptionName.append(channel_name)
                            #print(channel_name)
                            ChannelEncryptionSat.append(temp_SatName[index])
                            #print(temp_SatName[index])
                            ChannelEncryptionFreq.append(temp_freq[index])
                            # print(temp_freq[index])
                            ChannelEncryptionVideoEncod.append(VideoEncoding[index])
                            # print(VideoEncoding[index])
                        # print('==============')
                    elif len(parts) == 1:  
                        ChannelEncryption.append(parts[0])  
                        # print(f'Encryp: {parts[0]}')
                        # print(channel_name)
                        ChannelEncryptionName.append(channel_name)
                        ChannelEncryptionSat.append(temp_SatName[index])
                        # print(temp_SatName[index])
                        ChannelEncryptionFreq.append(temp_freq[index])
                        # print(temp_freq[index])
                        ChannelEncryptionVideoEncod.append(VideoEncoding[index])
                        # print(VideoEncoding[index])
                        # print('==============')
                    else:  # If the cell is empty, append "Unknown" once.
                        ChannelEncryption.append("Unknown")
                        # print(f'Encryp: Unknown')
                        ChannelEncryptionName.append(channel_name)
                        # print(channel_name)
                        ChannelEncryptionSat.append(temp_SatName[index])
                        # print(temp_SatName[index])
                        ChannelEncryptionFreq.append(temp_freq[index])
                        # print(temp_freq[index])
                        ChannelEncryptionVideoEncod.append(VideoEncoding[index])
                        # print(VideoEncoding[index])
                        # print('==============')
                    index += 1 
        maxLoops += 1

except Exception as e:
    print(f"Stopped at: {link}")
    filename = "ChannelBackup.csv"
    df_channel = pd.DataFrame({
    "SatName": SatelliteName,
    "ChannelName": ChannelName,
    "Frequency": Frequency,
    "VideoEncoding": VideoEncoding,
    "Website" : ChannelWebsite,
    "Beam": Beam,
    "VideoCompression": VideoCompression,
    "SR": SR,
    "FEC": FEC,
    "EIRP": EIRP
})
    df_channel = df_channel.drop_duplicates()
    df_channel.to_csv("filename", index=False)
    print(f"An error occurred: {e}")
finally:
    driver6.quit()





KeyboardInterrupt: 

In [273]:
for i in range(len(ChannelName)):
    print(ChannelName[i])

Udaya Movies
Udaya Movies
Udaya Movies
Udaya Movies
Udaya Movies
Udaya Movies
Udaya Movies
Animal Planet Polska
Eurobet Canale Azzurro
CT 1
Ihsan TV
Naftemporiki TV
Naftemporiki TV
Travel TV
Travel TV
Travel TV
Travel TV
Bloomberg TV Australia
Star World Middle East
Star World Middle East
Televisiete
Televisiete
Televisiete
Televisiete
Valiasr-aj TV
BFBS Sport
BFBS Sport
BFBS Sport
BFBS Sport
BFBS Sport
Vice TV West
Ahsan TV
Ahsan TV
E-Vidya 67
Hope Channel Ethiopia
World Revival Mission
TVC Deportes 2
Sport Klub HD
Mini TV
K CN 2
K CN 2
K CN 2
Light TV
Light TV
SEC Network
SEC Network
SEC Network
SEC Network
SEC Network
SEC Network
SEC Network
SEC Network
SEC Network
KITE VICTERS Plus
Detective Jam
Showtime West
Showtime West
Showtime West
Showtime West
Showtime West
Showtime West
Showtime West
Bet 9JA Stadium Serie A
Film Mánia
Film Mánia
Film Mánia
Film Mánia
MLB Extra Innings 6
MLB Extra Innings 6
MLB Extra Innings 6
MLB Extra Innings 6
MLB Extra Innings 6
MLB Extra Innings 6
MLB E

Adding Extracted data to csv files

In [274]:
print(f"Channel names: {len(ChannelName)}")
print(f"Satellite name: {len(SatelliteName)}")
print(f"Frequency: {len(Frequency)}")
print(f"VideoEncoding: {len(VideoEncoding)}")
print(f"Website: {len(ChannelWebsite)}")
print(f"Beam: {len(Beam)}")
print(f"VideoCompression: {len(VideoCompression)}")
print(f"SR: {len(SR)}")
print(f"FEC: {len(FEC)}")
print(f"EIRP: {len(EIRP)}")


print(f"ChSysName: {len(ChannelSystemName)}")
print(f"ChSysSat: {len(ChannelSystemSat)}")
print(f"ChSysFreq: {len(ChannelSystemFreq)}")
print(f"ChSysVidEncod: {len(ChannelSystemVideoEncod)}")
print(f"ChSys: {len(ChannelSystem)}")


print(f"ChLanName: {len(ChannelLanguageName)}")
print(f"ChLanSat: {len(ChannelLanguageSat)}")
print(f"ChLanFreq: {len(ChannelLanguageFreq)}")
print(f"ChLanVidEncod: {len(ChannelLanguageVideoEncod)}")
print(f"ChLan: {len(ChannelLanguage)}")

print(f"ChEncrName: {len(ChannelEncryptionName)}")
print(f"ChEncrSat: {len(ChannelEncryptionSat)}")
print(f"ChEncrFreq: {len(ChannelEncryptionFreq)}")
print(f"ChEncrVidEncod: {len(ChannelEncryptionVideoEncod)}")
print(f"ChEncr: {len(ChannelEncryption)}")


df_channel = pd.DataFrame({
    "SatName": SatelliteName,
    "ChannelName": ChannelName,
    "Frequency": Frequency,
    "VideoEncoding": VideoEncoding,
    "Website" : ChannelWebsite,
    "Beam": Beam,
    "VideoCompression": VideoCompression,
    "SR": SR,
    "FEC": FEC,
    "EIRP": EIRP
})

df_countries = pd.DataFrame({
    "SatName": ChannelCountriesSat,
    "ChannelName": ChannelCountriesName,
    "Frequency": ChannelCountriesFreq,
    "VideoEncoding": ChannelCountriesVideoEncod,
    "Countries": ChannelCountries
})

df_system = pd.DataFrame({
    "SatName": ChannelSystemSat,
    "ChannelName": ChannelSystemName,
    "Frequency": ChannelSystemFreq,
    "VideoEncoding": ChannelSystemVideoEncod,
    "Systems": ChannelSystem
})

df_language = pd.DataFrame({
    "SatName": ChannelLanguageSat,
    "ChannelName": ChannelLanguageName,
    "Frequency": ChannelLanguageFreq,
    "VideoEncoding": ChannelLanguageVideoEncod,
    "Languages": ChannelLanguage
})

df_encryption = pd.DataFrame({
    "SatName": ChannelEncryptionSat,
    "ChannelName": ChannelEncryptionName,
    "Frequency": ChannelEncryptionFreq,
    "VideoEncoding": ChannelEncryptionVideoEncod,
    "Encryptions": ChannelEncryption
})

# Remove duplicates
df_channel = df_channel.drop_duplicates()
df_countries = df_countries.drop_duplicates()
df_system = df_system.drop_duplicates()
df_language = df_language.drop_duplicates()
df_encryption = df_encryption.drop_duplicates()

# Save to CSV
df_channel.to_csv("Channel.csv", index=False)
df_countries.to_csv("ChannelCountries.csv", index=False)
df_system.to_csv("ChannelSystems.csv", index=False)
df_language.to_csv("ChannelLanguages.csv", index=False)
df_encryption.to_csv("ChannelEncryptions.csv", index=False)

Channel names: 42545
Satellite name: 42545
Frequency: 42545
VideoEncoding: 42545
Website: 42545
Beam: 42545
VideoCompression: 42545
SR: 42545
FEC: 42545
EIRP: 42545
ChSysName: 72740
ChSysSat: 72740
ChSysFreq: 72740
ChSysVidEncod: 72740
ChSys: 72740
ChLanName: 46352
ChLanSat: 46352
ChLanFreq: 46352
ChLanVidEncod: 46352
ChLan: 46352
ChEncrName: 56787
ChEncrSat: 56787
ChEncrFreq: 56787
ChEncrVidEncod: 56787
ChEncr: 56787


Checking for Duplicates

In [276]:
from collections import defaultdict
def find_duplicate_entries(file_path, column_indices):
    """
    Finds and returns all duplicate entries across specified columns of a CSV file.

    :param file_path: Path to the CSV file.
    :param column_indices: List of indices of the columns to check for duplicates (0-based).
    :return: A dictionary where the keys are the duplicate values (as tuples) and the values are lists of row numbers where the duplicates were found.
    """
    with open(file_path, mode='r', encoding='utf-8') as file:
        reader = csv.reader(file)
        value_occurrences = defaultdict(list)  # Stores row indices for each composite value
        for row_index, row in enumerate(reader, start=1):  # Start counting rows from 1
            # Create a tuple of the values in the specified columns
            composite_value = tuple(row[index] for index in column_indices)
            value_occurrences[composite_value].append(row_index)

    # Filter out entries with only one occurrence to identify duplicates
    duplicates = {value: indices for value, indices in value_occurrences.items() if len(indices) > 1}

    return duplicates

print("Channel")
duplicates = find_duplicate_entries("Channel.csv", [0,1,2,3])
print(duplicates)

Channel
{('EchoStar 10', 'WJPX-TV', '12574 R', 'SD'): [835, 836], ('Thaicom 8', 'Thainess TV', '11680 H', 'HD'): [1563, 1564], ('Thor 6', 'Kanal 5', '10778 V', 'HD'): [1942, 25257], ('EchoStar 10', 'CNBC US', '12545 R', 'HD'): [2253, 2254], ('EchoStar 10', 'Paramount Network East', '12545 R', 'HD'): [2553, 2554], ('EchoStar 10', 'Cartoon Network East', '12501 L', 'HD'): [2607, 2608], ('EchoStar 10', 'WKAQ-TV', '12574 R', 'SD'): [2871, 2872], ('EchoStar 10', 'The Weather Channel', '12472 L', 'HD'): [3054, 3055], ('QuetzSat 1', 'TV Méxiquense', '12276 R', 'HD 1080'): [3149, 3150], ('Eutelsat 16A', 'Alfa TV', '10972 V', 'SD'): [3493, 8191], ('ChinaSat 6D', 'Hunan TV', '3760 H', 'HD'): [3582, 3583], ('Hispasat 30W-6', 'Cubavisión Nacional', '11884 V', 'SD'): [4206, 4207], ('Star One C4', 'Canal 2', '11130 V', 'SD'): [4459, 12985], ('EchoStar 14', 'BBC America East', '12253 R', 'HD'): [4470, 4471], ('EchoStar 10', 'Animal Planet East', '12545 R', 'HD'): [4804, 4805], ('EchoStar 10', 'WSJX-L

Removing Duplicate primary keys from channel

In [279]:
def remove_duplicates_and_save(df_channel):
    # Define the columns to use for identifying duplicates
    primary_key_columns = ["SatName", "ChannelName", "Frequency", "VideoEncoding"]

    # Remove duplicate rows based on the combination of the primary key columns
    df_cleaned = df_channel.drop_duplicates(subset=primary_key_columns, keep='first')

    # Write the cleaned DataFrame to a CSV file, without index
    df_cleaned.to_csv("Channel.csv", index=False)

    return df_cleaned

# Example usage:
# Assuming SatelliteName, ChannelName, Frequency, VideoEncoding, ChannelWebsite, Beam, VideoCompression, SR, FEC, EIRP are already defined
# and df_channel is defined as a DataFrame with these columns

cleaned_df = remove_duplicates_and_save(df_channel)


In [282]:
duplicates = find_duplicate_entries("Channel.csv", [0,1,2,3])
print(duplicates)
print("==================")
print("ChannelCountries")
duplicates = find_duplicate_entries("ChannelCountries.csv", [0,1,2,3,4])
print(duplicates)
print("==================")
print("ChannelSystemVideoEncod")
duplicates = find_duplicate_entries("ChannelSystems.csv", [0,1,2,3,4])
print(duplicates)
print("==================")
print("ChannelLanguage")
duplicates = find_duplicate_entries("ChannelLanguages.csv", [0,1,2,3,4])
print(duplicates)
print("==================")
print("ChannelEncryption")
duplicates = find_duplicate_entries("ChannelEncryptions.csv", [0,1,2,3,4])
print(duplicates)

{}
ChannelCountries
{}
ChannelSystemVideoEncod
{}
ChannelLanguage
{}
ChannelEncryption
{}


Extracting Networks Attributes

In [289]:
driver7 = webdriver.Chrome(service=Service(ChromeDriverManager().install()), options=options)
stealth(driver7,
    languages=["en-US", "en"],
    vendor="Google Inc.",
    platform="Win32",
    webgl_vendor="Intel Inc.",
    renderer="Intel Iris OpenGL Engine",
    fix_hairline=True,
)

NetworkName = []
NetworkNameXpath = '/html/body/div/table/tbody/tr/td[2]/table[1]/tbody/tr[1]/td/font/b/font'


NetworkWebsite = []
NetworkWebsiteXpath1 = '/html/body/div/table/tbody/tr/td[2]/table[5]/tbody/tr/td[1]/font[1]/a'
NetworkWebsiteXpath2 = '/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[1]/font[1]/a'

NetworkCountryName = []
NetworkCountrySat = []
NetworkCountryFreq = []
NetworkCountryCountries = []
NetworkCountryXpaths = [
    '/html/body/div/table/tbody/tr/td[2]/table[5]/tbody/tr/td[1]/font[2]/a',
    '/html/body/div/table/tbody/tr/td[2]/table[5]/tbody/tr/td[1]/font[2]/a[1]',
    '/html/body/div/table/tbody/tr/td[2]/table[5]/tbody/tr/td[1]/font[2]/a[2]',
    '/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[1]/font[2]/a',
    '/html/body/div/table/tbody/tr/td[2]/table[5]/tbody/tr/td[1]/font/a'
]


# NetworkedNetworkName =[]
# NetworkedNetworkSat = []
# NetworkedNetworkFreq = []
# NetworkedChannels = []
# NetworkedChannelsXpath = '/html/body/div/table/tbody/tr/td[2]/p/table[1]/tbody/tr/td/font/span/a'
# NetworkedChannelLinks = []

#============================================================================================

SatelliteName = []
SatelliteXpath = ['/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[2]/font/span/a', '/html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr/td[2]/font/span/a']

Frequency = []
FrequencyXpath = ['/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[4]/font', '/html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr/td[4]/font']

Beam = []
BeamXpath = ['/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[3]/font', '/html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr/td[3]/font']    

EIRP = []

SR = []
SRXpath = ['/html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr/td[6]/font', '/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[6]/font']

/html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr/td[1]/font/font[1]/b/a
FEC = []

NetworkSystemName = []
NetworkSystemSat = []
NetworkSystemFreq = []
NetworkSystem = []
SystemXpath = ['/html/body/div/table/tbody/tr/td[2]/table[9]/tbody/tr/td[5]/font', '/html/body/div/table/tbody/tr/td[2]/table[7]/tbody/tr/td[5]/font']

try:
    for link in ExtractedNetworksLinks:
        driver7.get(link)

        temp_SatName = []
        temp_freq = []
        
        i =0
        for xpath in SatelliteXpath:
            satellite_elements = driver7.find_elements(By.XPATH, xpath)
            for satellite_element in satellite_elements:
                satellite_link = satellite_element.get_attribute('href')
                if not satellite_link.startswith('https://www.lyngsat.com/stream'):
                    i = i +1
                    SatelliteName.append(satellite_element.text)
                    temp_SatName.append(satellite_element.text)
                    SatEl = satellite_element.text
                    print(satellite_element.text)
        
        j = 0
        netname_elements = driver7.find_elements(By.XPATH, NetworkNameXpath)
        network_name = netname_elements[0].text if netname_elements else "Unknown"
        while j < i:
            NetworkName.append(network_name)
            print(network_name)
            j += 1 
            
        for xpath in FrequencyXpath:
            frequecny_elements = driver7.find_elements(By.XPATH, xpath)
            for frequency_element in frequecny_elements:
                if frequency_element.text != "Frequency":
                    Frequency.append(frequency_element.text)
                    temp_freq.append(frequency_element.text)
                    FreqEl = frequency_element.text
                    print(frequency_element.text)

        j = 0
        netweb_elements = driver7.find_elements(By.XPATH, NetworkWebsiteXpath1) or driver7.find_elements(By.XPATH, NetworkWebsiteXpath2)
        if netweb_elements and not netweb_elements[0].get_attribute('href').startswith("https://www.lyngsat.com/freetv"):
            website_url = netweb_elements[0].get_attribute('href')
        else:
            website_url = "null"
        while j < i:
            NetworkWebsite.append(website_url)
            print(website_url)
            j += 1
               
        found_countries = set()
        for xpath in NetworkCountryXpaths:
            netcountry_elements = driver7.find_elements(By.XPATH, xpath)
            for element in netcountry_elements:
                if element.get_attribute('href').startswith("https://www.lyngsat.com/freetv"):
                    country_name = element.text
                    found_countries.add(country_name)


        if not found_countries:
            found_countries.add("Unknown")

        NetworkCountryCountries.extend(found_countries)
        NetworkCountryName.extend([network_name] * len(found_countries))
        NetworkCountrySat.extend([SatEl] * len(found_countries))
        NetworkCountryFreq.extend([FreqEl] * len(found_countries))
        # print([network_name] * len(found_countries))
        # print(found_countries)

        # Find networked channels
        # found_channels = []
        # channel_elements = driver7.find_elements(By.XPATH, NetworkedChannelsXpath)
        # for element in channel_elements:
        #     channel_name = element.text
        #     NetworkedChannelLink = element.get_attribute('href')
        #     if NetworkedChannelLink.startswith("https://www.lyngsat.com/tvchannels"):
        #         NetworkedChannelLinks.append(NetworkedChannelLink)
        #     
        #         

        # if found_channels:
        #     NetworkedChannel.extend(found_channels)
        #     NetworkedNetworkName.extend([network_name] * len(found_channels))
        #     NetworkedNetworkSat.extend([SatEl] * len(found_channels))
        #     NetworkedNetworkFreq.extend([FreqEl] * len(found_channels))
        #     # print([network_name] * len(found_channels))
        #     # print(found_channels)
        # else:
        #     # Default related channel to the current channel name if none found
        #     NetworkedChannel.append("Unknown")
        #     NetworkedNetworkName.append(network_name)
        #     NetworkedNetworkSat.append(SatEl)
        #     NetworkedNetworkFreq.append(FreqEl)
            

        
                        
        for xpath in BeamXpath:
            Beam_elements = driver7.find_elements(By.XPATH, xpath)
            j = 0
            for Beam_element in Beam_elements:
                if Beam_element.text != 'Beam\nEIRP (dBW)':
                    Beam_text = Beam_element.text.strip()
                            
                    if not Beam_text:
                        if j < i:
                            Beam.append("null")
                            EIRP.append("null")
                            # print(f'Beam: null')
                            # print(f'EIRP: null')
                            j += 1
                    else:
                        parts = Beam_text.split('\n')
                            
                        if len(parts) == 2:
                            if j < i:
                                Beam.append(parts[0])
                                EIRP.append(parts[1])
                                # print(f'Beam: {parts[0]}')
                                # print(f'EIRP: {parts[1]}')
                                j += 1
                        elif len(parts) == 1:
                            if parts[0][0].isdigit():
                                if j < i:
                                    EIRP.append(parts[0])
                                    Beam.append("null")
                                    # print(f'Beam: null')
                                    # print(f'EIRP: {parts[0]}')
                                    j += 1
                            else:
                                if j < i:
                                    Beam.append(parts[0])
                                    EIRP.append("null")
                                    # print(f'Beam: {parts[0]}')
                                    # print(f'EIRP: null')
                                    j += 1
                                        
        for xpath in SRXpath:
            sr_fec_elements = driver7.find_elements(By.XPATH, xpath)
            for sr_fec_element in sr_fec_elements:
                if sr_fec_element.text != "SR\nFEC":
                    text = sr_fec_element.text.strip()
                        
                    # Initialize default values for SR and FEC
                    sr = "null"
                    fec = "null"
                        
                    # Split the text by '\n'
                    parts = text.split('\n')
                        
                    # Check if SR part exists and contains digits, otherwise assign "null"
                    if len(parts) > 0 and any(char.isdigit() for char in parts[0]):
                        sr = parts[0]
                        
                    # Check if FEC part exists and contains digits or a '/', otherwise assign "null"
                    if len(parts) > 1 and (any(char.isdigit() for char in parts[1]) or '/' in parts[1]):
                        fec = parts[1]
        
                    # Append the values or "null" to the respective lists
                    SR.append(sr)
                    FEC.append(fec)
        
                    #print(f'SR: {sr}, FEC: {fec}')    
                        
        index = 0            
        for xpath in SystemXpath:
            system_elements = driver7.find_elements(By.XPATH, xpath)
            for system_element in system_elements:
                systemCount = 0
                if system_element.text != 'System':
                    system_text = system_element.text.strip()
                        
                    # Split based on space for systems like "DVB-S2 8PSK"
                    parts = system_text.split('\n') if system_text else []
                        
                    if len(parts) == 2:  # If there are two parts, append them separately.
                        NetworkSystem.append(parts[0])  # Appending DVB-S2
                        NetworkSystem.append(parts[1])  # Appending 8PSK
                        systemCount += 2
                        # print(f'System: {parts[0]}')
                        # print(f'System: {parts[1]}')
                        NetworkSystemName.append(network_name)
                        NetworkSystemName.append(network_name)
                        # print(network_name)
                        # print(network_name)
                        NetworkSystemSat.append(temp_SatName[index])
                        NetworkSystemSat.append(temp_SatName[index])
                        # print(temp_SatName[index])
                        # print(temp_SatName[index])
                        NetworkSystemFreq.append(temp_freq[index])
                        NetworkSystemFreq.append(temp_freq[index])
                        # print(temp_freq[index])
                        # print(temp_freq[index])
                        # print('==============')
                    elif len(parts) == 1:  # If there's only one part, append it.
                        NetworkSystem.append(parts[0])  # Appending the single part
                        # print(f'System: {parts[0]}')
                        NetworkSystemName.append(network_name)
                        # print(network_name)
                        NetworkSystemSat.append(temp_SatName[index])
                        # print(temp_SatName[index])
                        NetworkSystemFreq.append(temp_freq[index])
                        # print(temp_freq[index])
                        # print('==============')
                        systemCount += 1
                    else:  # If the cell is empty, append "Unknown" once.
                        NetworkSystem.append("Unknown")
                        NetworkSystemName.append(network_name)
                        # print(network_name)
                        NetworkSystemSat.append(temp_SatName[index])
                        # print(temp_SatName[index])
                        NetworkSystemFreq.append(temp_freq[index])
                        # print(temp_freq[index])
                        # print('System: Unknown')
                        # print('==============')
                    index += 1
        
except Exception as e:
    print(f"An error occurred: {e}")
finally:
    driver7.quit()

# print(f"Total network names: {len(NetworkName)}")
# print(f"Total Websites: {len(NetworkWebsite)}")
# print(f"Total Countries: {len(NetworkCountryCountries)}")
# print(f"Total Channel names for countries: {len(NetworkCountryName)}")
# print(f"Total Related channels: {len(NetworkedChannel)}")
# print(f"Total Related channel names: {len(NetworkedNetworkName)}")

Optus D2
Optus D2
ABC SA
ABC SA
12470 H
12658 H
https://www.abc.net.au/
https://www.abc.net.au/
Hotbird 13F
Mediawan Thematics
12692 H
https://mediawan.fr/
Telkom 4
Indosat Ooredoo Hutchison
4080 H
https://indosatooredoo.com/
Badr 8
Profen
12092 V
https://profen.com/
ABS 3A
BT Media Group
11058 V
null
Badr 8
Es'hail 2
Nilesat 201
Al Kass
Al Kass
Al Kass
12245 V
10770 H
11919 H
https://www.alkass.net/
https://www.alkass.net/
https://www.alkass.net/
Eutelsat 65 West A
Eutelsat 65 West A
Record Litoral e Vale
Record Litoral e Vale
4545 H
4750 H
https://recordtv.r7.com/record-tv-litoral-e-vale
https://recordtv.r7.com/record-tv-litoral-e-vale
Al Yah 1
Hotbird 13G
Eutelsat 9B
Arqiva
Arqiva
Arqiva
11996 V
11137 H
12092 H
http://www.arqiva.com/
http://www.arqiva.com/
http://www.arqiva.com/
Galaxy 32
MASN
4010 H
https://www.masnsports.com/
Express AM7
RTRS Makhachkala
3715 L
https://www.rtrs.ru/
Star One C3
Band Amazonas
3984 V
https://www.band.uol.com.br/
Express AM6
RTRS Smolensk
10853 V
null

Placing Data in CSV files

In [447]:
print(f"NetworkName: {len(NetworkName)}")
print(f"SatelliteName: {len(SatelliteName)}")
print(f"Frequency: {len(Frequency)}")
print(f"Website: {len(NetworkWebsite)}")
print(f"Beam: {len(Beam)}")
print(f"SR: {len(SR)}")
print(f"FEC: {len(FEC)}")
print(f"EIRP: {len(EIRP)}")

print(f"NetworkName: {len(NetworkCountryName)}")
print(f"SatName: {len(NetworkCountrySat)}")
print(f"Frequency: {len(NetworkCountryFreq)}")
print(f"Countries: {len(NetworkCountryCountries)}")

print(f"NetworkSystemName: {len(NetworkSystemName)}")
print(f"NetworkSystemSat: {len(NetworkSystemSat)}")
print(f"NetworkSystemFreq: {len(NetworkSystemFreq)}")
print(f"NetworkSystem: {len(NetworkSystem)}")


df_network = pd.DataFrame({
    "NetName": NetworkName,
    "SatName": SatelliteName,
    "Frequency": Frequency,
    "Website": NetworkWebsite,
    "Beam": Beam,
    "SR": SR,
    "FEC": FEC,
    "EIRP": EIRP
})
df_networkcountries = pd.DataFrame({
    "NetName": NetworkCountryName,
    "SatName": NetworkCountrySat,
    "Frequency": NetworkCountryFreq,
    "Countries": NetworkCountryCountries
})

# df_belongsto = pd.DataFrame({
#     "NetworkName": NetworkedNetworkName,
#     "ChannelName": NetworkedChannel
# })



df_networksystems = pd.DataFrame({
    "NetName": NetworkSystemName,
    "SatName": NetworkSystemSat,
    "Frequency": NetworkSystemFreq,
    "Systems": NetworkSystem,
})

# Remove duplicates
df_network = df_network.drop_duplicates()
df_networkcountries = df_networkcountries.drop_duplicates()
# df_belongsto = df_belongsto.drop_duplicates()
df_networksystems = df_networksystems.drop_duplicates()


# Save to CSV
df_network.to_csv("Network.csv", index=False)
df_networkcountries.to_csv("NetworkCountries.csv", index=False)
# df_belongsto.to_csv("BelongsTo.csv", index=False)
df_networksystems.to_csv("NetworkSystems.csv", index=False)

NetworkName: 1537
SatelliteName: 1537
Frequency: 1537
Website: 1537
Beam: 1537
SR: 1537
FEC: 1537
EIRP: 1537
NetworkName: 772
SatName: 772
Frequency: 772
Countries: 772
NetworkSystemName: 2697
NetworkSystemSat: 2697
NetworkSystemFreq: 2697
NetworkSystem: 2697


Checking For Duplicates on primary key

In [294]:
print("Networks")
duplicates = find_duplicate_entries("Network.csv", [0,1,2])
print(duplicates)
print("==================")
print("NetworkCountries")
duplicates = find_duplicate_entries("NetworkCountries.csv", [0,1,2,3])
print(duplicates)
print("==================")
print("NetworkSystems")
duplicates = find_duplicate_entries("NetworkSystems.csv", [0,1,2,3])
print(duplicates)
print("==================")

Networks
{}
NetworkCountries
{}
NetworkSystems
{}


Extracting Data For NetworkChannel

In [358]:
from selenium.common.exceptions import NoSuchElementException
driver8 = webdriver.Chrome(service=Service(ChromeDriverManager().install()), options=options)
stealth(driver8,
    languages=["en-US", "en"],
    vendor="Google Inc.",
    platform="Win32",
    webgl_vendor="Intel Inc.",
    renderer="Intel Iris OpenGL Engine",
    fix_hairline=True,
)

def extract_up_to_last_at(s):
    # Find the index of the last occurrence of "at" in the string
    at_index = s.rfind('at')
    
    # If "at" is found, extract the substring and trim spaces before "at"
    if at_index != -1:
        return s[:at_index].rstrip()
    else:
        return s

SatelliteXpath = '/html/body/div/table/tbody/tr/td[2]/table[1]/tbody/tr[1]/td/font/b/font'

NetworkedChannelsName= []
NetworkedChannelsSatName = []
NetworkedChannelsFrequency = []
NetworkedChannelsVideoEncod = []
NetworkedChannels = []

try:
    for link in ExtractedSatLinks:
        driver8.get(link)
        tables = driver8.find_elements(By.XPATH, '/html/body/div/table/tbody/tr/td[2]/table')
        channels = set()
        for table in tables:
            rows = table.find_elements(By.XPATH,'./tbody/tr')
            for row in rows:
            # Check if the first cell has a rowspan attribute

                rowspan_cell = row.find_elements(By.XPATH,'./td[1][@rowspan]')
                if rowspan_cell:
                    freq = row.find_element(By.XPATH,'./td[1]/font/font/b')
                    freq_value = freq.text
                    for rs in rowspan_cell:
                        rowspan_value = int(rs.get_attribute('rowspan'))
                        # print("Rowspan value:", rowspan_value)
                    # Find the other cell on the same row
                    other_cell = row.find_elements(By.XPATH,'./td')
                    for other_cells in other_cell:
                        othercells = other_cells.find_elements(By.XPATH,'./font/font/b/i/a')
                        for cell in othercells:
                            if 'providers' in cell.get_attribute('href'):
                                x = 0
                                providerName = cell.text
                                SatelliteElement = driver8.find_element(By.XPATH, SatelliteXpath)
                                SatelliteExtracted = extract_up_to_last_at(SatelliteElement.text)
                                # Both conditions are met, perform further actions here
                                for i in range(1, rowspan_value):
                                    
                                    corresponding_row = rows[rows.index(row) + i]
                                    
                                    corresponding_cell = corresponding_row.find_element(By.XPATH,f'./td[{othercells.index(cell) + 2}]')
                                    corresponding_cell_text = corresponding_cell.text

                                    corresponding_cell_encoding = corresponding_row.find_element(By.XPATH,f'./td[{othercells.index(cell) + 4}]')
                                    corresponding_cell_encoding_value = corresponding_cell_encoding.text
                                    corresponding_cell_link =  corresponding_row.find_elements(By.XPATH,f'./td[{othercells.index(cell) + 2}]//a') 
                                    if corresponding_cell_link:
                                        corresponding_cell_href = corresponding_cell_link[0].get_attribute('href')
                                        
                                        if corresponding_cell_href  and corresponding_cell_href.startswith('https://www.lyngsat.com/tvchannels'):
                                            NetworkedChannels.append(corresponding_cell_text)
                                            NetworkedChannelsVideoEncod.append(corresponding_cell_encoding_value[-2:])
                                            NetworkedChannelsName.append(providerName)
                                            print(SatelliteExtracted)
                                            print(providerName)
                                            NetworkedChannelsSatName.append(SatelliteExtracted)
                                            # print(f'Corresponding cell text for row {rows.index(row) + i} and column {othercells.index(cell) + 2}: {corresponding_cell_text}')
                                            x+=1
                                NetworkedChannelsFrequency.extend([freq_value]*x)  
                                print([freq_value]*x)
                                # You can access the text content of the other cell, etc.
except Exception as e:
    print(f"An error occurred: {e}")
finally:
    driver8.quit()

NSS 9
American Forces Network
NSS 9
American Forces Network
NSS 9
American Forces Network
['4055 L', '4055 L', '4055 L']
Intelsat 18
American Forces Network
Intelsat 18
American Forces Network
Intelsat 18
American Forces Network
Intelsat 18
American Forces Network
Intelsat 18
American Forces Network
Intelsat 18
American Forces Network
Intelsat 18
American Forces Network
Intelsat 18
American Forces Network
Intelsat 18
American Forces Network
['3753 R', '3753 R', '3753 R', '3753 R', '3753 R', '3753 R', '3753 R', '3753 R', '3753 R']
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
Anuvu
Intelsat 18
An

Placing in CSV File

In [361]:
print(f"NetworkName: {len(NetworkedChannelsName)}")
print(f"SatName: {len(NetworkedChannelsSatName)}")
print(f"Frequency: {len(NetworkedChannelsFrequency)}")
print(f"VideoEncoding: {len(NetworkedChannelsVideoEncod)}")
print(f"NetworkedChannels: {len(NetworkedChannels)}")

df_NetworkedChannels = pd.DataFrame({
    "NetName": NetworkedChannelsName,
    "SatName ": NetworkedChannelsSatName,
    "Frequncy ": NetworkedChannelsFrequency,
    "ChannelVideoEncoding ": NetworkedChannelsVideoEncod,
    "NetworkedChannels ": NetworkedChannels,
})


df_NetworkedChannels = df_NetworkedChannels.drop_duplicates()

df_NetworkedChannels.to_csv("NetworkedChannels.csv", index=False)

NetworkName: 10228
SatName: 10228
Frequency: 10228
VideoEncoding: 10228
NetworkedChannels: 10228


Checking For Duplicates

In [362]:
print("Networks")
duplicates = find_duplicate_entries("NetworkedChannels.csv", [0,1,2,3,4])

Networks


Generating Users

In [363]:
def generate_unique_email(name, domain, existing_emails):
    email = f"{name.lower()}.{random.randint(1, 1000)}@{domain}"
    while email in existing_emails:
        email = f"{name.lower()}.{random.randint(1, 1000)}@{domain}"
    existing_emails.add(email)
    return email

def generate_password():
    vowels = "aeiou"
    consonants = "".join(set(string.ascii_lowercase) - set(vowels))
    text_chars = "".join(random.choice(consonants) + random.choice(vowels) for _ in range(5))
    number = random.choice(string.digits)
    symbol = random.choice('!@#$%^&*-')
    password = f"{text_chars}{number}{symbol}"
    return password

def generate_user(existing_usernames, existing_emails):
    male_names = [
        'Youssef', 'Khaled', 'Yassin', 'Omar', 'Ahmed', 'Mohamed', 'Yasser', 'Jack', 'Cris', 'Mike', 'Ross', 'Chandler',
        'John', 'Wei', 'Ivan', 'Kenji', 'Lucas', 'Raj', 'Jayden', 'Mateo', 'Liam', 'Noah'
    ]
    female_names = [
        'Nour', 'Mariam', 'Hana', 'Sara', 'Lina', 'Malak', 'Nagham', 'Rachel', 'Monica', 'Phoebe', 'Emily', 'Maria',
        'Aisha', 'Anna', 'Sophia', 'Isabella', 'Amelia', 'Chloe', 'Olivia'
    ]

    country_region_map = {
        'Egypt': 'Africa & Middle East', 'United States': 'North & South America', 'China': 'Asia & Pacific',
        'Brazil': 'North & South America', 'Russia': 'Europe, Africa & Middle East', 'India': 'Asia & Pacific',
        'Japan': 'Asia & Pacific', 'Germany': 'Europe, Africa & Middle East', 'Nigeria': 'Africa & Middle East',
        'France': 'Europe, Africa & Middle East', 'Australia': 'Asia & Pacific', 'Canada': 'North & South America',
        'South Korea': 'Asia & Pacific', 'Italy': 'Europe, Africa & Middle East', 'Mexico': 'North & South America',
        'United Kingdom': 'Europe, Africa & Middle East', 'Turkey': 'Europe, Africa & Middle East',
        'Spain': 'Europe, Africa & Middle East', 'South Africa': 'Africa & Middle East', 'Indonesia': 'Asia & Pacific', 'United Arab Emirates': 'Asia & Pacific', 'Saudi Arabia': 'Asia & Pacific', 'Jordan': 'Asia & Pacific', 'Finland': 'Europe, Africa & Middle East', 'Norway': 'Europe, Africa & Middle East'
    }

    if random.choice(['M', 'F']) == 'M':
        name = random.choice(male_names)
        gender = 'M'
    else:
        name = random.choice(female_names)
        gender = 'F'

    username = f"{name}{random.randint(1, 100)}"
    while username in existing_usernames:
        username = f"{name}{random.randint(1, 100)}"
    existing_usernames.add(username)

    email = generate_unique_email(name, "example.com", existing_emails)
    password = generate_password()
    birthdate = datetime.now() - timedelta(days=random.randint(18, 70) * 365)
    country = random.choice(list(country_region_map.keys()))
    region = country_region_map[country]

    return {
        'username': username,
        'email': email,
        'password': password,
        'gender': gender,
        'birthdate': birthdate.strftime('%Y-%m-%d'),
        'country': country,
        'region': region
    }

def generate_users_and_save_to_csv(file_path, user_count=100):
    existing_usernames = set()
    existing_emails = set()
    users = [generate_user(existing_usernames, existing_emails) for _ in range(user_count)]

    with open(file_path, 'w', newline='') as file:
        writer = csv.DictWriter(file, fieldnames=['username', 'email', 'password', 'gender', 'birthdate', 'country', 'region'])
        writer.writeheader()
        for user in users:
            writer.writerow(user)


file_path = 'Users.csv'
generate_users_and_save_to_csv(file_path)

print(f"Users have been saved to {file_path}.")


Users have been saved to Users.csv.


Generating User Favorites

In [444]:
import csv
import random

def read_channel_data(channel_file_path):
    with open(channel_file_path, mode='r', encoding='utf-8') as file:
        csv_reader = csv.DictReader(file)
        rows = list(csv_reader)
        if rows:
            random_row = random.choice(rows)
            return {
                'SatName': random_row['SatName'],
                'ChannelName': random_row['ChannelName'],
                'Frequency': random_row['Frequency'],
                'VideoEncoding': random_row['VideoEncoding']
            }
        else:
            return {}

def extract_emails_from_csv(file_path):
    with open(file_path, mode='r', encoding='utf-8') as file:
        csv_reader = csv.reader(file)
        next(csv_reader)  # Skip the header row
        return [row[1] for row in csv_reader if len(row) > 1]

def assign_favorite_channels(user_emails, channel_file_path):
    user_favorites = {}

    for email in user_emails:
        # Read a different random channel data for each user inside the loop
        channel_data = read_channel_data(channel_file_path)
        user_favorites[email] = channel_data

    return user_favorites

def save_favorites_to_csv(user_favorites, output_file_path):
    with open(output_file_path, mode='w', encoding='utf-8', newline='') as file:
        writer = csv.writer(file)
        writer.writerow(['UserEmail', 'SatName', 'ChannelName', 'Frequency', 'VideoEncoding'])
        for email, channels in user_favorites.items():
            writer.writerow([email, channels['SatName'], channels['ChannelName'], channels['Frequency'], channels['VideoEncoding']])

# Paths to the files
user_file_path = 'Users.csv'
channel_file_path = 'Channel.csv'
output_file_path = 'Favorite.csv'

# Extract user emails and assign favorite channels
user_emails = extract_emails_from_csv(user_file_path)
user_favorites = assign_favorite_channels(user_emails, channel_file_path)

# Save the assigned favorite channels to Favorite.csv
save_favorites_to_csv(user_favorites, output_file_path)

print(f"Favorite channels have been saved to {output_file_path}.")


Favorite channels have been saved to Favorite.csv.


In [391]:
import pandas as pd

def compare_satellites_and_channels(satellites_file, channels_file):
    # Read the CSV files into DataFrames
    satellites_df = pd.read_csv(satellites_file)
    channels_df = pd.read_csv(channels_file)

    # Get the sets of names from each file
    satellite_names = set(satellites_df['Name'])
    channel_sat_names = set(channels_df['SatName'])

    # Find names in satellite file not in channel file and vice versa
    not_in_channels = satellite_names.difference(channel_sat_names)
    not_in_satellites = channel_sat_names.difference(satellite_names)

    return not_in_channels, not_in_satellites

# Path to the CSV files
satellites_file = 'Satellites.csv'
channels_file = 'Channel.csv'

# Get the unique names
not_in_channels, not_in_satellites = compare_satellites_and_channels(satellites_file, channels_file)


print("Names in Channel.csv not in Satellites.csv:", not_in_satellites)


Names in Channel.csv not in Satellites.csv: set()


In [399]:

def remove_rows_and_save(file_path, column_name, values_to_remove):

    df = pd.read_csv(file_path)


    filtered_df = df[~df[column_name].isin(values_to_remove)]


    filtered_df.to_csv(file_path, index=False)


file_path = 'ChannelSystems.csv'
column_name = 'SatName'
values_to_remove = {'T10/T12', 'T11/T14', 'T9S/T16'}

remove_rows_and_save(file_path, column_name, values_to_remove)


In [402]:
import pandas as pd

def remove_blank_channel_names(file_path):
    # Load the CSV file into a DataFrame
    df = pd.read_csv(file_path)

    # Remove rows where 'ChannelName' is blank or empty
    df = df[df['ChannelName'].notna() & (df['ChannelName'] != '')]

    # Write the updated DataFrame back to the same CSV file
    df.to_csv(file_path, index=False)

# Path to your CSV file
file_path = 'ChannelCountries.csv'

# Call the function to remove rows with blank 'ChannelName' and rewrite the file
remove_blank_channel_names(file_path)

In [438]:
import pandas as pd

def remove_unmatched_rows(channel_file, channel_countries_file):
    # Load the CSV files into DataFrames
    channel_df = pd.read_csv(channel_file)
    channel_countries_df = pd.read_csv(channel_countries_file)

    # Create a unique identifier for each row by concatenating the values of the composite key columns
    channel_df['unique_key'] = channel_df['NetName'] 
    channel_countries_df['unique_key'] = channel_countries_df['NetName']

    # Find the keys that are in ChannelCountries but not in Channel
    unmatched_keys = set(channel_countries_df['unique_key']) - set(channel_df['unique_key'])

    # Filter out these unmatched rows from ChannelCountries
    filtered_channel_countries_df = channel_countries_df[~channel_countries_df['unique_key'].isin(unmatched_keys)]

    # Drop the temporary 'unique_key' column as it's no longer needed
    filtered_channel_countries_df = filtered_channel_countries_df.drop(columns=['unique_key'])

    # Save the updated DataFrame back to ChannelCountries.csv
    filtered_channel_countries_df.to_csv(channel_countries_file, index=False)

# Define the file paths
channel_file = 'Network.csv'
channel_countries_file = 'NetworkedChannels.csv'

# Call the function
remove_unmatched_rows(channel_file, channel_countries_file)


In [458]:
import pandas as pd

def remove_unmatched_network_rows(network_file, network_countries_file):
    # Load the CSV files into DataFrames
    network_df = pd.read_csv(network_file)
    network_countries_df = pd.read_csv(network_countries_file)

    network_df['unique_key'] = network_df['NetName'] + '|' + network_df['SatName'] + '|' + network_df['Frequency'].astype(str)
    network_countries_df['unique_key'] = network_countries_df['NetName'] + '|' + network_countries_df['SatName'] + '|' + network_countries_df['Frequency'].astype(str)

    # Find the keys that are in NetworkCountries but not in Network
    unmatched_keys = set(network_countries_df['unique_key']) - set(network_df['unique_key'])

    filtered_network_countries_df = network_countries_df[~network_countries_df['unique_key'].isin(unmatched_keys)]


    filtered_network_countries_df = filtered_network_countries_df.drop(columns=['unique_key'])

    filtered_network_countries_df.to_csv(network_countries_file, index=False)


network_file = 'Network.csv'
network_countries_file = 'NetworkedChannels.csv'

# Call the function to remove unmatched rows
remove_unmatched_network_rows(network_file, network_countries_file)


Popultae the database

In [461]:
def Populate2():
    Names = ["Satellite", "Channel", "ChannelCountries", "ChannelSystems", "ChannelLanguages", "ChannelEncryptions", "Network", "NetworkCountries", "NetworkSystems", "User", "Favorite", "NetworkedChannels",]
    CSV = ["Satellites.csv", "Channel.csv", "ChannelCountries.csv", "ChannelSystems.csv", "ChannelLanguages.csv", "ChannelEncryptions.csv", "Network.csv", "NetworkCountries.csv", "NetworkSystems.csv", "Users.csv", "Favorite.csv", "NetworkedChannels.csv"]
    for i in range(len(CSV)):
        df = pd.read_csv(CSV[i], encoding="utf-8")
        df = df.where(pd.notna(df), None)

        db_user = "root"
        db_password = "Macthor21"
        db_host = "localhost"
        db_port = "3306"
        db_name = "TV_BroadCast"

        engine_str = f"mysql+pymysql://{db_user}:{db_password}@{db_host}:{db_port}/{db_name}"
        engine = create_engine(engine_str)
        table_name = Names[i]
        df.to_sql(table_name, con=engine, if_exists="append", index=False)
        engine.dispose()

Handling Duplicates

Calling Populate

In [462]:
Populate2()